In [1]:
import pandas as pd
import requests
from bs4 import BeautifulSoup
from dateutil import parser
import matplotlib.pyplot as plt
from textblob import TextBlob
from collections import Counter
from openpyxl import Workbook

ModuleNotFoundError: No module named 'textblob'

In [2]:
pip install textblob

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 636.8/636.8 kB 323.6 kB/s eta 0:00:00a 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [8]:
base_url = "https://www.airlinequality.com/airline-reviews/british-airways"
pagesize = 100 
pages = 37
airline = "BA"
region = "Europe"

# Create empty lists for ratings
categories = ['Seat Comfort', 'Cabin Staff Service', 'Food & Beverages', 
              'Inflight Entertainment', 'Ground Service', 'Wifi & Connectivity','Value For Money']
ratings = {category: [] for category in categories}

# Create an empty DataFrame
db = pd.DataFrame(columns=['Date_of_Review', 'Region', 'Airline', 'Title', 'Rating', 'Date Flown', 'Aircraft','Type_of_Traveller',
                           'Seat_Type','Route','Recommended', 'Review'] + categories)

for i in range(1, pages + 1):
    url = f"{base_url}/page/{i}/?sortby=post_date%3ADesc&pagesize={pagesize}"
    response = requests.get(url)
    content = response.content
    soup = BeautifulSoup(content, 'html.parser')

    for div in soup.find_all("article", itemprop="review"):
        rating = div.find("span", itemprop="ratingValue")
        rating = rating.text if rating else "N/A"
        
        title = div.find("h2", class_="text_header").get_text().strip('"')
        
        date = div.find("time", itemprop="datePublished")
        date = parser.parse(date.text).strftime('%Y-%m-%d') if date else "N/A"        
        
        review = div.find("div", class_="text_content").get_text().strip('✅')
        
        aircraft = div.find("td", class_="review-rating-header aircraft")
        aircraft = aircraft.find_next("td", class_="review-value").text if aircraft else "N/A"
        
        traveller = div.find("td", class_="review-rating-header type_of_traveller")
        traveller = traveller.find_next("td", class_="review-value").text if traveller else "N/A"
        
        seat_type = div.find("td", class_="review-rating-header cabin_flown")
        seat_type = seat_type.find_next("td", class_="review-value").text if seat_type else "N/A"
        
        route = div.find("td", class_="review-rating-header route")
        route = route.find_next("td", class_="review-value").text if route else "N/A"

        date_flown = div.find("td", text="Date Flown")
        date_flown = parser.parse(date_flown.find_next("td", class_="review-value").text).strftime('%Y-%m') if date_flown else "N/A"

        recommended = div.find("td", class_="review-rating-header recommended")
        recommended = recommended.find_next("td", class_=lambda x: x and x.startswith("review-value rating-")).text if recommended else "N/A"

        category_values = {}

        for category in categories:
            category_values[category] = "N/A"

        for row in div.find_all('tr'):
            header = row.find('td', class_='review-rating-header').text
            value = len(row.find_all('span', class_='star fill')) if row.find_all('span', class_='star fill') else "N/A"
            if header in categories:
                category_values[header] = value

        # Append the data to the DataFrame
        db_new_row = pd.DataFrame({
            'Aircraft':[aircraft],
            'Type_of_Traveller':[traveller],
            'Seat_Type':[seat_type],
            'Route':[route],
            'Region': [region],
            'Airline': [airline],
            'Rating': [rating],
            'Title': [title],
            'Date_of_Review': [date],
            'Review': [review],
            'Date Flown': [date_flown],
            'Recommended': [recommended],
            **category_values
        })

        db = pd.concat([db, db_new_row], ignore_index=True)


Date_of_Review  Region Airline                                    Title   
0        2023-10-31  Europe      BA               “BA clearly does not care”  \
1        2023-10-28  Europe      BA  reflect a downward trend of the airline   
2        2023-10-24  Europe      BA                 One of my better flights   
3        2023-10-23  Europe      BA             I would still recommend BA"    
4        2023-10-22  Europe      BA                the worst experience ever   
...             ...     ...     ...                                      ...   
3685     2012-08-29  Europe      BA          British Airways customer review   
3686     2012-08-28  Europe      BA          British Airways customer review   
3687     2011-10-12  Europe      BA          British Airways customer review   
3688     2011-10-11  Europe      BA          British Airways customer review   
3689     2011-10-09  Europe      BA          British Airways customer review   

     Rating Date Flown  Aircraft Type_of_Traveller        Seat_Type   
0         1    2023-10       N/A    Couple Leisure    Economy Class  \
1         6    2023-10      A320      Solo Leisure    Economy Class   
2         8    2023-10       N/A    Couple Leisure    Economy Class   
3         7    2023-10  A321 neo          Business    Economy Class   
4         1    2023-10       N/A    Couple Leisure    Economy Class   
...     ...        ...       ...               ...              ...   
3685      5        N/A       N/A               N/A   Business Class   
3686      9        N/A       N/A               N/A   Business Class   
3687      5        N/A       N/A               N/A    Economy Class   
3688      4        N/A       N/A               N/A  Premium Economy   
3689      4        N/A       N/A               N/A      First Class   

                                    Route Recommended   
0     Anchorage to Heathrow via Barcelona          no  \
1            London Heathrow to Gibraltar          no   
2                  London to Philadelphia         yes   
3                London Heathrow to Cairo         yes   
4           Seattle to Porto via Heathrow          no   
...                                   ...         ...   
3685                                  N/A         yes   
3686                                  N/A         yes   
3687                                  N/A         yes   
3688                                  N/A          no   
3689                                  N/A          no   

                                                 Review Seat Comfort   
0      Trip Verified |   1. Ground crew in Heathrow ...            3  \
1      Trip Verified |  London Heathrow to Gibraltar...            3   
2      Trip Verified | First time flying British Air...            4   
3     Not Verified |  I flew London to Cairo and ret...            3   
4     Not Verified |  Absolutely the worst experienc...            2   
...                                                 ...          ...   
3685  Flew return in CW from LHR to BKK in August 20...            4   
3686  LHR to HAM. Purser addresses all club passenge...            4   
3687  My son who had worked for British Airways urge...          N/A   
3688  London City-New York JFK via Shannon on A318 b...            1   
3689  SIN-LHR BA12 B747-436 First Class. Old aircraf...            4   

     Cabin Staff Service Food & Beverages Inflight Entertainment   
0                      3                3                      3  \
1                      1                1                    N/A   
2                      5                4                      3   
3                      5                3                    N/A   
4                      3                3                      3   
...                  ...              ...                    ...   
3685                   3                2                      4   
3686                   5                4                    N/A   
3687                 N/A     

In [9]:
csv_file_name = f'{airline}_reviews.csv'
db.to_csv(csv_file_name, index=False)

## Define a function to implement the scrapping

In [3]:


def scrape_airline_reviews(base_url, pagesize, pages, airline, region):
    # Create empty lists for ratings
    categories = ['Seat Comfort', 'Cabin Staff Service', 'Food & Beverages', 
                  'Inflight Entertainment', 'Ground Service', 'Wifi & Connectivity','Value For Money']
    ratings = {category: [] for category in categories}

    # Create an empty DataFrame
    db = pd.DataFrame(columns=['Date_of_Review', 'Region', 'Airline', 'Title', 'Rating', 'Date Flown', 'Aircraft','Type_of_Traveller',
                               'Seat_Type','Route','Recommended', 'Review'] + categories)

    for i in range(1, pages + 1):
        url = f"{base_url}/page/{i}/?sortby=post_date%3ADesc&pagesize={pagesize}"
        response = requests.get(url)
        content = response.content
        soup = BeautifulSoup(content, 'html.parser')

        for div in soup.find_all("article", itemprop="review"):
            rating = div.find("span", itemprop="ratingValue")
            rating = rating.text if rating else "N/A"
            
            title = div.find("h2", class_="text_header").get_text().strip('"')
            
            date = div.find("time", itemprop="datePublished")
            date = parser.parse(date.text).strftime('%Y-%m-%d') if date else "N/A"        
            
            review = div.find("div", class_="text_content").get_text().strip('✅')
            
            aircraft = div.find("td", class_="review-rating-header aircraft")
            aircraft = aircraft.find_next("td", class_="review-value").text if aircraft else "N/A"
            
            traveller = div.find("td", class_="review-rating-header type_of_traveller")
            traveller = traveller.find_next("td", class_="review-value").text if traveller else "N/A"
            
            seat_type = div.find("td", class_="review-rating-header cabin_flown")
            seat_type = seat_type.find_next("td", class_="review-value").text if seat_type else "N/A"
            
            route = div.find("td", class_="review-rating-header route")
            route = route.find_next("td", class_="review-value").text if route else "N/A"

            date_flown = div.find("td", text="Date Flown")
            date_flown = parser.parse(date_flown.find_next("td", class_="review-value").text).strftime('%Y-%m') if date_flown else "N/A"

            recommended = div.find("td", class_="review-rating-header recommended")
            recommended = recommended.find_next("td", class_=lambda x: x and x.startswith("review-value rating-")).text if recommended else "N/A"

            category_values = {}

            for category in categories:
                category_values[category] = "N/A"

            for row in div.find_all('tr'):
                header = row.find('td', class_='review-rating-header').text
                value = len(row.find_all('span', class_='star fill')) if row.find_all('span', class_='star fill') else "N/A"
                if header in categories:
                    category_values[header] = value

            # Append the data to the DataFrame
            db_new_row = pd.DataFrame({
                'Aircraft':[aircraft],
                'Type_of_Traveller':[traveller],
                'Seat_Type':[seat_type],
                'Route':[route],
                'Region': [region],
                'Airline': [airline],
                'Rating': [rating],
                'Title': [title],
                'Date_of_Review': [date],
                'Review': [review],
                'Date Flown': [date_flown],
                'Recommended': [recommended],
                **category_values
            })

            db = pd.concat([db, db_new_row], ignore_index=True)  

    return db

### List all the airlines

In [4]:
# List of airlines with their respective information
airlines = [
    {
        "name": "Spirit_Airlines",
        "url": "https://www.airlinequality.com/airline-reviews/spirit-airlines",
        "pagesize": 100,
        "pages": 51,
        "region": "North_America"
    },
    {        
        "name": "Turkish_Airlines",
        "url": "https://www.airlinequality.com/airline-reviews/turkish-airlines",
        "pagesize": 100,
        "pages": 25,
        "region": "Europe"
    },
    {        
        "name": "Ryanair",
        "url": "https://www.airlinequality.com/airline-reviews/ryanair",
        "pagesize": 100,
        "pages": 23,
        "region": "Europe"
    },
    {        
        "name": "China_Southern_Airlines",
        "url": "https://www.airlinequality.com/airline-reviews/china-southern-airlines",
        "pagesize": 100,
        "pages": 20,
        "region": "China"
    },
    {        
        "name": "Norwegian",
        "url": "https://www.airlinequality.com/airline-reviews/norwegian",
        "pagesize": 100,
        "pages": 14,
        "region": "Europe"
    },
        {        
        "name": "Air_France",
        "url": "https://www.airlinequality.com/airline-reviews/air-france",
        "pagesize": 100,
        "pages": 14,
        "region": "Europe"
    },    
    {        
        "name": "Jetstar Airways",
        "url": "https://www.airlinequality.com/airline-reviews/jetstar-airways",
        "pagesize": 100,
        "pages": 13,
        "region": "Australia/Pacific"
    },
    {        
        "name": "Air_India",
        "url": "https://www.airlinequality.com/airline-reviews/air-india",
        "pagesize": 100,
        "pages": 13,
        "region": "Asia"
    },
        {        
        "name": "Air_Canada_rouge",
        "url": "https://www.airlinequality.com/airline-reviews/air-canada-rouge",
        "pagesize": 100,
        "pages": 13,
        "region": "North_America"
    }
]


### Run the function and concatenate them into a single DataFrame

In [5]:
all_reviews = pd.DataFrame()

# Loop through each airline
for airline_info in airlines:
    airline_name = airline_info["name"]
    base_url = airline_info["url"]
    pagesize = airline_info["pagesize"]
    pages = airline_info["pages"]
    region = airline_info["region"]

    # Call the function for scraping reviews
    reviews = scrape_airline_reviews(base_url, pagesize, pages, airline_name, region)

    # Concatenate the reviews to the combined DataFrame
    all_reviews = pd.concat([all_reviews, reviews], ignore_index=True)

# Save the combined DataFrame to a CSV file
all_reviews.to_csv('combined_airline_reviews.csv', index=False)

/var/folders/hs/5y6_hx2d04sgkgfqz21z92zr0000gn/T/ipykernel_1106/1739157397.py:40: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  date_flown = div.find("td", text="Date Flown")
/var/folders/hs/5y6_hx2d04sgkgfqz21z92zr0000gn/T/ipykernel_1106/1739157397.py:40: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  date_flown = div.find("td", text="Date Flown")
/var/folders/hs/5y6_hx2d04sgkgfqz21z92zr0000gn/T/ipykernel_1106/1739157397.py:40: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  date_flown = div.find("td", text="Date Flown")
/var/folders/hs/5y6_hx2d04sgkgfqz21z92zr0000gn/T/ipykernel_1106/1739157397.py:40: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  date_flown = div.find("td", text="Date Flown")
/var/folders/hs/5y6_hx2d04sgkgfqz21z92zr0000gn/T/ipykernel_1106/1739157397.p

In [7]:
all_reviews.to_csv('all_reviews.csv')

In [8]:
all_reviews

Date_of_Review         Region           Airline  \
0         2023-11-16  North_America   Spirit_Airlines   
1         2023-11-16  North_America   Spirit_Airlines   
2         2023-11-15  North_America   Spirit_Airlines   
3         2023-11-15  North_America   Spirit_Airlines   
4         2023-11-15  North_America   Spirit_Airlines   
...              ...            ...               ...   
18133     2014-01-20  North_America  Air_Canada_rouge   
18134     2014-01-20  North_America  Air_Canada_rouge   
18135     2014-01-10  North_America  Air_Canada_rouge   
18136     2014-01-10  North_America  Air_Canada_rouge   
18137     2014-01-02  North_America  Air_Canada_rouge   

                                              Title Rating Date Flown  \
0         will pay extra for less hassle and stress      1    2023-11   
1                  never consider flying them again      1    2023-11   
2        low cost airline who hides the bigger cost      1    2023-11   
3                 have always had a good experience      9    2023-10   
4      Refused reimbursement for a cancelled flight      2    2023-09   
...                                             ...    ...        ...   
18133              Air Canada rouge customer review      1        N/A   
18134              Air Canada rouge customer review      1        N/A   
18135              Air Canada rouge customer review      1        N/A   
18136              Air Canada rouge customer review      1        N/A   
18137              Air Canada rouge customer review      2        N/A   

         Aircraft Type_of_Traveller        Seat_Type  \
0      Boeing 737      Solo Leisure    Economy Class   
1            A320    Family Leisure    Economy Class   
2             N/A      Solo Leisure    Economy Class   
3            A321      Solo Leisure    Economy Class   
4             N/A      Solo Leisure    Economy Class   
...           ...               ...              ...   
18133         N/A               N/A    Economy Class   
18134         N/A               N/A  Premium Economy   
18135         N/A               N/A    Economy Class   
18136         N/A               N/A    Economy Class   
18137         N/A               N/A    Economy Class   

                                 Route Recommended  \
0      Fort Lauderdale to Indianapolis          no   
1            Columbus to Ft Lauderdale          no   
2                 Las Vegas to Atlanta          no   
3                     Detroit to Tampa         yes   
4                Newark to Los Angeles          no   
...                                ...         ...   
18133                              N/A          no   
18134                              N/A          no   
18135                              N/A          no   
18136                              N/A          no   
18137                              N/A          no   

                                                  Review Seat Comfort  \
0      Not Verified |  Scales not accurate, at kiosk ...            1   
1      Not Verified |  Stuck for 1 hr 30 mins in the ...            3   
2       Trip Verified | Spirit Airline, (S-pirate) lo...            2   
3      Not Verified |  I have flown Spirit Airlines o...            3   
4       Trip Verified |  Refused reimbursement for a ...          N/A   
...                                                  ...          ...   
18133  My husband and I recently took AC Rouge to Can...            1   
18134  YYZ-LAS. In a word-terrible and to be avoided....            1   
18135  We fly Orlando to Toronto twice a year every y...            1   
18136  Toronto to Punta Cana and back to Toronto. Rou...            1   
18137  We flew Air Canada Rouge Airbus to Samana. It ...            1   

      Cabin Staff Service Food & Beverages Inflight Entertainment  \
0                       4              N/A                    N/A   
1                       2              N/A                    N/A   
2                       1             

In [10]:
airlines = [
    {
        "name": "Lufthansa",
        "url": "https://www.airlinequality.com/airline-reviews/lufthansa",
        "pagesize": 100,
        "pages": 24,
        "region": "Europe"
    }]

In [11]:
all_reviews = pd.DataFrame()

# Loop through each airline
for airline_info in airlines:
    airline_name = airline_info["name"]
    base_url = airline_info["url"]
    pagesize = airline_info["pagesize"]
    pages = airline_info["pages"]
    region = airline_info["region"]

    # Call the function for scraping reviews
    reviews = scrape_airline_reviews(base_url, pagesize, pages, airline_name, region)

    # Concatenate the reviews to the combined DataFrame
    all_reviews = pd.concat([all_reviews, reviews], ignore_index=True)

# Save the combined DataFrame to a CSV file
all_reviews.to_csv('Lufthansa.csv', index=False)

/var/folders/hs/5y6_hx2d04sgkgfqz21z92zr0000gn/T/ipykernel_1106/1739157397.py:40: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  date_flown = div.find("td", text="Date Flown")
/var/folders/hs/5y6_hx2d04sgkgfqz21z92zr0000gn/T/ipykernel_1106/1739157397.py:40: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  date_flown = div.find("td", text="Date Flown")
/var/folders/hs/5y6_hx2d04sgkgfqz21z92zr0000gn/T/ipykernel_1106/1739157397.py:40: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  date_flown = div.find("td", text="Date Flown")
/var/folders/hs/5y6_hx2d04sgkgfqz21z92zr0000gn/T/ipykernel_1106/1739157397.py:40: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  date_flown = div.find("td", text="Date Flown")
/var/folders/hs/5y6_hx2d04sgkgfqz21z92zr0000gn/T/ipykernel_1106/1739157397.p

In [13]:
all_reviews.head()

Date_of_Review  Region    Airline                            Title Rating  \
0     2023-11-15  Europe  Lufthansa               such a low service      1   
1     2023-11-11  Europe  Lufthansa        Good service throughout"      10   
2     2023-11-04  Europe  Lufthansa  service has deteriorated lately      1   
3     2023-10-29  Europe  Lufthansa     farce of Priority boarding"       1   
4     2023-10-24  Europe  Lufthansa       no customer service at all      2   

  Date Flown Aircraft Type_of_Traveller       Seat_Type  \
0    2023-11      N/A      Solo Leisure   Economy Class   
1    2023-10      N/A          Business  Business Class   
2    2023-10      N/A          Business  Business Class   
3    2023-10      N/A          Business   Economy Class   
4    2023-08      N/A      Solo Leisure  Business Class   

                             Route Recommended  \
0  Hamburg to Lisbon via Frankfurt          no   
1   Dublin to Kraków via Frankfurt         yes   
2              Madrid to Frankfurt          no   
3            Frankfurt to Budapest          no   
4               Munich to New York          no   

                                              Review Seat Comfort  \
0   Trip Verified | It is very sad to experience ...            2   
1  Not Verified |   Good service throughout. Meal...            4   
2   Trip Verified |  I am shocked how much their ...            1   
3   Trip Verified |   They do the farce of Priori...            2   
4  Not Verified | Wating for luggage took more th...            3   

  Cabin Staff Service Food & Beverages Inflight Entertainment Ground Service  \
0                   2              N/A                    N/A              3   
1                   5                3                    N/A              4   
2                   2                1                      1              4   
3                   4              N/A                      1              1   
4                   5                4                      3              3   

  Wifi & Connectivity Value For Money  
0                 N/A               1  
1                   5               4  
2                   1               1  
3                   1               1  
4                 N/A               1

In [18]:
import numpy as np
split_data = all_reviews['Review'].str.split('|', n=1, expand=True)
all_reviews['Status'] = None  # Initialize 'Status' column as None
all_reviews['Reviews'] = split_data[0]  # Default assignment
for i, row in split_data.iterrows():
    if row[1] is not None:
        all_reviews.at[i, 'Status'] = row[0]
        all_reviews.at[i, 'Reviews'] = row[1]
    else:
        all_reviews.at[i, 'Status'] = np.nan
all_reviews = all_reviews.drop(columns="Review")

In [22]:
all_reviews.head()

Date_of_Review  Region    Airline                            Title Rating  \
0     2023-11-15  Europe  Lufthansa               such a low service      1   
1     2023-11-11  Europe  Lufthansa        Good service throughout"      10   
2     2023-11-04  Europe  Lufthansa  service has deteriorated lately      1   
3     2023-10-29  Europe  Lufthansa     farce of Priority boarding"       1   
4     2023-10-24  Europe  Lufthansa       no customer service at all      2   

  Date Flown Aircraft Type_of_Traveller       Seat_Type  \
0    2023-11      N/A      Solo Leisure   Economy Class   
1    2023-10      N/A          Business  Business Class   
2    2023-10      N/A          Business  Business Class   
3    2023-10      N/A          Business   Economy Class   
4    2023-08      N/A      Solo Leisure  Business Class   

                             Route Recommended Seat Comfort  \
0  Hamburg to Lisbon via Frankfurt          no            2   
1   Dublin to Kraków via Frankfurt         yes            4   
2              Madrid to Frankfurt          no            1   
3            Frankfurt to Budapest          no            2   
4               Munich to New York          no            3   

  Cabin Staff Service Food & Beverages Inflight Entertainment Ground Service  \
0                   2              N/A                    N/A              3   
1                   5                3                    N/A              4   
2                   2                1                      1              4   
3                   4              N/A                      1              1   
4                   5                4                      3              3   

  Wifi & Connectivity Value For Money           Status  \
0                 N/A               1   Trip Verified    
1                   5               4    Not Verified    
2                   1               1   Trip Verified    
3                   1               1   Trip Verified    
4                 N/A               1    Not Verified    

                                             Reviews  
0   It is very sad to experience Lufthansa gettin...  
1     Good service throughout. Meals could be a b...  
2    I am shocked how much their service has dete...  
3     They do the farce of Priority boarding whic...  
4   Wating for luggage took more than 1 hour in M...

## Pre-defined clustering multi label + no threshold

In [26]:
all_reviews.groupby('Seat_Type').size()

Seat_Type
Business Class      528
Economy Class      1628
First Class          81
N/A                   1
Premium Economy     126
dtype: int64

In [27]:
all_reviews.head(100).to_csv("test.csv")

In [ ]:
import pandas as pd
import numpy as np
from gensim.models import KeyedVectors
from sklearn.metrics.pairwise import cosine_similarity
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import gensim.downloader as api



# 加载nltk的停用词库
stop_words = set(stopwords.words('english'))

def preprocess_text(text):
    # 分词并转换为小写
    words = word_tokenize(text.lower())
    # 删除停用词
    words = [word for word in words if word.isalpha() and word not in stop_words]
    return ' '.join(words)

# 假设您已经有了预定义的标签列表
predefined_labels = ['seat comfort ', 'staff service ', 'food ', 'entertainment', 'wifi', 'ground service', 'value for money', 'Flight Delay Cancel']  # 标签列表

# 加载数据
reviews = all_reviews['Reviews']

# 预处理评论和标签
processed_reviews = [preprocess_text(review) for review in reviews]
processed_labels = [preprocess_text(label) for label in predefined_labels]

# 加载预训练的Word2Vec模型
model = api.load('word2vec-google-news-300')

def vectorize_text(text, model):
    vectors = [model[word] for word in text.split() if word in model]
    if len(vectors) == 0:
        return np.zeros(model.vector_size)
    return np.mean(vectors, axis=0)

# 向量化评论和标签
review_vectors = np.array([vectorize_text(review, model) for review in processed_reviews])
label_vectors = np.array([vectorize_text(label, model) for label in processed_labels])

# 计算相似度并分配标签
similarity_threshold = 0  # 设置一个相似度阈值
assigned_labels = []

for review_vector in review_vectors:
    similarities = cosine_similarity([review_vector], label_vectors)[0]
    review_labels = [predefined_labels[i] for i in np.where(similarities > similarity_threshold)[0]]
    assigned_labels.append(review_labels)

# 将分配的标签添加到DataFrame
all_reviews['Assigned Labels'] = assigned_labels


[=======-------------------------------------------] 14.8% 246.6/1662.8MB downloaded

In [29]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
reviews = all_reviews['Reviews']

# Text Preprocessing and Vectorization
vectorizer = TfidfVectorizer(stop_words='english', lowercase=True)
review_vectors = vectorizer.fit_transform(reviews)

In [38]:
label

0      1      2      3      4      5      6      7      8      9      \
0       0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1       0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2       0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
3       0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4       0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2359    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2360    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2361    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2362    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2363    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

      ...  10097  10098  10099  10100  10101  10102  10103  10104  10105  \
0     ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1     ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2     ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
3     ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4     ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...   ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
2359  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2360  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2361  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2362  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2363  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

      10106  
0       0.0  
1       0.0  
2       0.0  
3       0.0  
4       0.0  
...     ...  
2359    0.0  
2360    0.0  
2361    0.0  
2362    0.0  
2363    0.0  

[2364 rows x 10107 columns]

In [45]:
reviews = all_reviews['Reviews']

In [44]:
from gensim.corpora import Dictionary
from gensim.models import LdaModel
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize


In [46]:
# Ensuring necessary NLTK downloads
nltk.download('punkt')
nltk.download('stopwords')

# Function to preprocess text
def preprocess_text(text):
    tokens = word_tokenize(text.lower())
    tokens = [token for token in tokens if token.isalpha() and token not in stopwords.words('english')]
    return tokens

# Preprocessing the reviews
preprocessed_reviews = reviews.apply(preprocess_text)

# Create a dictionary and corpus for LDA
dictionary = Dictionary(preprocessed_reviews)
dictionary.filter_extremes(no_below=20, no_above=0.6)
corpus = [dictionary.doc2bow(text) for text in preprocessed_reviews]

# Apply LDA
num_topics = 7  # Arbitrary choice, can be adjusted
lda_model = LdaModel(corpus=corpus, id2word=dictionary, num_topics=num_topics)

# Viewing the topics in LDA model
topics = lda_model.print_topics(num_words=5)
topics

[nltk_data] Downloading package punkt to /Users/hangyang/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/hangyang/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


[(0,
  '0.018*"frankfurt" + 0.018*"service" + 0.013*"crew" + 0.012*"lh" + 0.011*"airline"'),
 (1,
  '0.014*"class" + 0.013*"time" + 0.012*"one" + 0.012*"lh" + 0.012*"frankfurt"'),
 (2,
  '0.020*"good" + 0.016*"frankfurt" + 0.015*"seat" + 0.014*"service" + 0.014*"seats"'),
 (3,
  '0.029*"good" + 0.021*"service" + 0.019*"seats" + 0.015*"economy" + 0.013*"lh"'),
 (4,
  '0.029*"service" + 0.023*"good" + 0.020*"class" + 0.016*"business" + 0.013*"frankfurt"'),
 (5,
  '0.020*"seats" + 0.013*"food" + 0.013*"lh" + 0.012*"frankfurt" + 0.010*"time"'),
 (6,
  '0.024*"seat" + 0.016*"food" + 0.015*"class" + 0.015*"flights" + 0.014*"entertainment"')]

In [47]:
[lda_model.get_document_topics(bow) for bow in corpus]

[[(0, 0.94620484)],
 [(2, 0.7192327), (4, 0.2409119)],
 [(1, 0.28439024), (4, 0.5897355), (5, 0.1167633)],
 [(0, 0.013036541),
  (1, 0.34296498),
  (2, 0.013034152),
  (3, 0.013026662),
  (4, 0.013047941),
  (5, 0.0130229825),
  (6, 0.5918668)],
 [(1, 0.97734535)],
 [(0, 0.053934414), (1, 0.5766452), (6, 0.35985348)],
 [(1, 0.51212186), (4, 0.3684226), (6, 0.10901862)],
 [(1, 0.97795594)],
 [(1, 0.8019967), (5, 0.1800609)],
 [(1, 0.96557957)],
 [(1, 0.9795107)],
 [(3, 0.13227718), (4, 0.77415735), (5, 0.08704102)],
 [(0, 0.01024676),
  (1, 0.93807405),
  (2, 0.010711815),
  (3, 0.010250765),
  (4, 0.010243469),
  (5, 0.01024137),
  (6, 0.010231771)],
 [(5, 0.96557415)],
 [(0, 0.67535096), (1, 0.31521672)],
 [(1, 0.94399434), (2, 0.047147192)],
 [(0, 0.06359802), (1, 0.55240107), (2, 0.37443572)],
 [(1, 0.9785002)],
 [(0, 0.37812755), (1, 0.61372507)],
 [(1, 0.9804406)],
 [(4, 0.22253406), (6, 0.7376369)],
 [(0, 0.96559495)],
 [(3, 0.4187133), (5, 0.56420887)],
 [(1, 0.9398692), (5, 0.0